In [1]:
import matplotlib.pyplot as plt
import seaborn as sns
from keras.models import Sequential
from keras.layers import Dense, Conv2D , Conv1D, MaxPool1D, MaxPool2D , Flatten , Dropout , BatchNormalization
from keras.preprocessing.image import ImageDataGenerator
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report,confusion_matrix
import pandas as pd
from sklearn.preprocessing import LabelBinarizer
import joblib
import os
from PIL import Image
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import re
import numpy as np
from keras.models import Sequential
from keras.layers import Conv2D, MaxPool2D, MaxPooling2D, GlobalAveragePooling2D, BatchNormalization, Dropout, Dense, Flatten, Input, Lambda
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import ModelCheckpoint
from keras.callbacks import ReduceLROnPlateau , EarlyStopping
from tensorflow.keras.optimizers import Adam 
from tensorflow.keras import regularizers
import tensorflow as tf
from keras.utils.np_utils import to_categorical # convert to one-hot-encoding

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
import albumentations as A

transform = A.Compose([
    A.RandomBrightnessContrast(),
    A.Affine(scale=[0.8,1.2],translate_percent=0.05, shear=0.2, keep_ratio=True, p=0.5),
    A.Rotate(limit=10)
])

## Without mediapipe

#### Read image and convert it to 28x28 matrix:

In [ ]:
folder_name = '/content/drive/MyDrive/IS4242/data' #might be different for different people
path = folder_name
img_list = []
label_list = []
txt = 'abcdefghiklmnopqrstuvwxy'

for i in tqdm(range(len(os.listdir(path)))):
  filename = os.listdir(path)[i]
  if filename.endswith(('.jpg','.png')):
      label_name = re.split(r'[-_]', filename)[0].lower()
      if label_name not in txt:
        continue
      label_list.append(label_name)
      img = Image.open(os.path.join(path, filename))
      img = img.resize((28, 28), Image.ANTIALIAS)
      img = img.convert('L')
      img_array = np.array(img)
      
      img_list.append(img_array)


In [ ]:
X = np.array(img_list)

y = np.array(label_list)
y = np.array(list(map(lambda x:txt.find(x), y)))
y = to_categorical(y)

#### Train test split

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

output_dir = '/content/drive/MyDrive/IS4242/dump/'
joblib.dump(X, output_dir+'X.pkl')
joblib.dump(y, output_dir+'y.pkl')

(634, 28, 28)
(159, 28, 28)
(634, 24)
(159, 24)


['/content/drive/MyDrive/IS4242/dump/y.pkl']

#### Augmentation only on train data

In [ ]:
augmented_X = []
augmented_y = []
for i in range(len(X_train)):
  for j in (range(10)):
      transformed = transform(image=X_train[i])
      augmented_X.append(transformed['image'])
      augmented_y.append(y_train[i])

augmented_X = np.array(augmented_X)
augmented_y = np.array(augmented_y)
X_train = np.concatenate([X_train,augmented_X])
y_train = np.concatenate([y_train,augmented_y])

output_dir = '/content/drive/MyDrive/IS4242/dump/'
joblib.dump(augmented_X, output_dir+'augmented_X.pkl')
joblib.dump(augmented_y, output_dir+'augmented_y.pkl')

['/content/drive/MyDrive/IS4242/dump/augmented_y.pkl']

In [ ]:
print(X_train.shape)
print(y_train.shape)

(6974, 28, 28)
(6974, 24)


#### Reshape and divide the pixels by 255

In [ ]:
X_train = X_train/255.0
X_test = X_test/255.0
X_train = X_train.reshape(-1, 28, 28, 1)
X_test = X_test.reshape(-1, 28, 28, 1)

In [ ]:
print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(6974, 28, 28, 1)
(159, 28, 28, 1)
(6974, 24)
(159, 24)


#### CNN with augmentation

In [ ]:
datagen = ImageDataGenerator(
        featurewise_center=False,  # set input mean to 0 over the dataset
        samplewise_center=False,  # set each sample mean to 0
        featurewise_std_normalization=False,  # divide inputs by std of the dataset
        samplewise_std_normalization=False,  # divide each input by its std
        zca_whitening=False,  # apply ZCA whitening
        rotation_range=10,  # randomly rotate images in the range (degrees, 0 to 180)
        zoom_range = 0.1, # Randomly zoom image 
        width_shift_range=0.1,  # randomly shift images horizontally (fraction of total width)
        height_shift_range=0.1,  # randomly shift images vertically (fraction of total height)
        horizontal_flip=False,
        brightness_range=[0.8,1.2],
        vertical_flip=False)


datagen.fit(X_train)

In [ ]:
# Set a learning rate annealer
learning_rate_reduction = ReduceLROnPlateau(monitor='val_accuracy', 
                                            patience=3, 
                                            verbose=1, 
                                            factor=0.5, 
                                            min_lr=0.00001)

In [ ]:
# architecture
# Set the CNN model 

model = Sequential()
model.add(Conv2D(filters = 128, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu', input_shape = (28,28,1)))
model.add(Conv2D(filters = 128, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2)))
model.add(BatchNormalization())
model.add(Dropout(0.25))
model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2), strides=(2,2)))
model.add(BatchNormalization())
model.add(Dropout(0.25))
model.add(Conv2D(filters = 32, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(Conv2D(filters = 32, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(BatchNormalization())
model.add(MaxPool2D((2,2) , strides = 2 , padding = 'same'))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(512, activation = "relu"))
model.add(Dense(256, activation = "relu"))
model.add(Dense(24, activation = "softmax"))

model.compile(optimizer=Adam(lr=0.001), loss='categorical_crossentropy', metrics=['accuracy'])
model.summary()

Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_42 (Conv2D)          (None, 28, 28, 32)        832       
                                                                 
 conv2d_43 (Conv2D)          (None, 28, 28, 32)        25632     
                                                                 
 max_pooling2d_21 (MaxPoolin  (None, 14, 14, 32)       0         
 g2D)                                                            
                                                                 
 batch_normalization_21 (Bat  (None, 14, 14, 32)       128       
 chNormalization)                                                
                                                                 
 dropout_28 (Dropout)        (None, 14, 14, 32)        0         
                                                                 
 conv2d_44 (Conv2D)          (None, 14, 14, 64)       

In [ ]:
epochs = 30
batch_size = 32


model_checkpoint_callback = ModelCheckpoint(
    filepath="best.h5",
    monitor='val_accuracy', 
    verbose=1, 
    save_best_only=True, 
    mode='max')

es = EarlyStopping(monitor="val_loss", mode="min", verbose=1, patience=10)

# Fit the model
history = model.fit_generator(datagen.flow(X_train, y_train, batch_size=batch_size),
                              epochs = epochs, validation_data = (X_test, y_test),steps_per_epoch=X_train.shape[0] // batch_size,
                              verbose = 1,   callbacks=[model_checkpoint_callback,learning_rate_reduction,es])

Epoch 1/30


<ipython-input-169-021abc8791b3>:15: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  history = model.fit_generator(datagen.flow(X_train, y_train, batch_size=batch_size),


54/54 [==============================] - ETA: 0s - loss: 3.4244 - accuracy: 0.0540
Epoch 1: val_accuracy improved from -inf to 0.01887, saving model to best.h5
54/54 [==============================] - 81s 1s/step - loss: 3.4244 - accuracy: 0.0540 - val_loss: 3.2231 - val_accuracy: 0.0189 - lr: 0.0010
Epoch 2/30
54/54 [==============================] - ETA: 0s - loss: 3.1336 - accuracy: 0.0711
Epoch 2: val_accuracy improved from 0.01887 to 0.06289, saving model to best.h5
54/54 [==============================] - 82s 2s/step - loss: 3.1336 - accuracy: 0.0711 - val_loss: 3.2113 - val_accuracy: 0.0629 - lr: 0.0010
Epoch 3/30
54/54 [==============================] - ETA: 0s - loss: 3.0425 - accuracy: 0.0963
Epoch 3: val_accuracy did not improve from 0.06289
54/54 [==============================] - 77s 1s/step - loss: 3.0425 - accuracy: 0.0963 - val_loss: 3.2515 - val_accuracy: 0.0440 - lr: 0.0010
Epoch 4/30
54/54 [==============================] - ETA: 0s - loss: 2.8801 - accuracy: 0.1382
E

In [ ]:
results = model.predict(X_test)
y_pred = np.argmax(results,axis = 1) 
y_true = np.argmax(y_test,axis = 1) 


5/5 [==============================] - 0s 71ms/step


#### Results

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_true, y_pred))

              precision    recall  f1-score   support

           0       0.50      0.40      0.44         5
           1       0.25      0.40      0.31         5
           2       0.83      0.42      0.56        12
           3       0.50      0.40      0.44         5
           4       0.38      0.43      0.40         7
           5       0.57      0.67      0.62         6
           6       0.00      0.00      0.00         5
           7       0.25      0.09      0.13        11
           8       0.75      0.60      0.67         5
           9       0.75      0.50      0.60         6
          10       0.67      0.67      0.67         3
          11       0.00      0.00      0.00         3
          12       0.11      0.20      0.14         5
          13       0.57      0.50      0.53         8
          14       0.67      0.57      0.62         7
          15       0.33      0.17      0.22         6
          16       0.29      0.25      0.27         8
          17       0.50    

#### Prediction and evaluation

In [ ]:
img = Image.open('m.png')
img = img.resize((28, 28), Image.ANTIALIAS)
img = img.convert('L')
img_array = np.array(img)
img_array = img_array/255.0
img_array = img_array.reshape(-1, 28, 28, 1)

In [ ]:
results = model.predict(img_array)
y_pred = np.argmax(results,axis = 1)
txt[y_pred[0]]

1/1 [==============================] - 0s 46ms/step


'm'

#### After hyperparameter tuning, train it with the whole data

In [ ]:
output_dir = '/content/drive/MyDrive/IS4242/dump/'
X = joblib.load(output_dir+'X.pkl')
y = joblib.load(output_dir+'y.pkl')

In [ ]:
augmentX = []
augmenty = []
for i in range(len(X)):
  for j in (range(10)):
      transformed = transform(image=X[i])
      augmentX.append(transformed['image'])
      augmenty.append(y[i])

augmentX = np.array(augmentX)
augmenty = np.array(augmenty)
X = np.concatenate([X,augmentX])
y = np.concatenate([y,augmenty])

In [ ]:
X = X/255.0
X = X.reshape(-1, 28, 28, 1)

In [ ]:
datagen = ImageDataGenerator(
        featurewise_center=False,  # set input mean to 0 over the dataset
        samplewise_center=False,  # set each sample mean to 0
        featurewise_std_normalization=False,  # divide inputs by std of the dataset
        samplewise_std_normalization=False,  # divide each input by its std
        zca_whitening=False,  # apply ZCA whitening
        rotation_range=10,  # randomly rotate images in the range (degrees, 0 to 180)
        zoom_range = 0.1, # Randomly zoom image 
        width_shift_range=0.1,  # randomly shift images horizontally (fraction of total width)
        height_shift_range=0.1,  # randomly shift images vertically (fraction of total height)
        horizontal_flip=False,
        brightness_range=[0.8,1.2],
        vertical_flip=False)


datagen.fit(X)

In [ ]:
model = Sequential()
model.add(Conv2D(filters = 32, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu', input_shape = (28,28,1)))
model.add(Conv2D(filters = 32, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2) , padding = 'same'))
model.add(BatchNormalization())
model.add(Dropout(0.25))
model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2) , padding = 'same'))
model.add(BatchNormalization())
model.add(Dropout(0.25))
model.add(Conv2D(filters = 128, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(Conv2D(filters = 128, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(BatchNormalization())
model.add(MaxPool2D((2,2) , padding = 'same'))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(256, activation = "relu"))
model.add(Dense(512, activation = "relu"))
model.add(Dense(24, activation = "softmax"))

model.compile(optimizer=Adam(lr=0.001), loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
epochs = 30
batch_size = 64

# Fit the model
model.compile(optimizer=Adam(lr=0.001), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit_generator(datagen.flow(X, y, batch_size=batch_size),epochs = epochs)

In [ ]:
img = Image.open('m.png')
img = img.resize((28, 28), Image.ANTIALIAS)
img = img.convert('L')
img_array = np.array(img)
img_array = img_array/255.0
img_array = img_array.reshape(-1, 28, 28, 1)

In [ ]:
results = model.predict(img_array)
y_pred = np.argmax(results,axis = 1)
txt[y_pred[0]]

1/1 [==============================] - 0s 46ms/step


'm'

## Using mediapipe

In [4]:
!pip install mediapipe

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.6/33.6 MB 43.5 MB/s eta 0:00:00


In [5]:
# For capturing hand coordinates
import cv2
import tensorflow as tf
import mediapipe as mp

In [6]:
# For processing data
import csv
import os
import numpy as np
import pandas as pd
from tqdm import tqdm 
import re

#### Convert image data to matrix

In [ ]:
from google.colab import drive
drive.mount('/content/drive', force_remount = True)

Mounted at /content/drive


In [ ]:
import albumentations as A

transform = A.Compose([
    A.RandomBrightnessContrast(),
    A.Affine(scale=[0.8,1.2],translate_percent=0.05, shear=0.2, keep_ratio=True, p=0.5),
    A.Rotate(limit=10)
])

In [ ]:
folder_name = '/content/drive/MyDrive/IS4242/data' #might be different for different people
path = folder_name
img_list = []
label_list = []
txt = 'abcdefghiklmnopqrstuvwxy'

for i in tqdm(range(len(os.listdir(path)))):
  filename = os.listdir(path)[i]
  if filename.endswith(('.jpg','.png')):
      label_name = re.split(r'[-_]', filename)[0].lower()
      if label_name not in txt:
        continue
      label_list.append(label_name)
      img = Image.open(os.path.join(path, filename))
      img = img.resize((224, 224), Image.ANTIALIAS) # bigger size
      img = img.convert('L')
      img_array = np.array(img)
      
      img_list.append(img_array)

X = np.array(img_list)

y = np.array(label_list)
y = np.array(list(map(lambda x:txt.find(x), y)))
y = to_categorical(y)

output_dir = '/content/drive/MyDrive/IS4242/dump/'
joblib.dump(X,output_dir+'X_224.pkl')
joblib.dump(y,output_dir+'y_224.pkl')


 16%|█▌        | 196/1221 [00:26<03:02,  5.63it/s]

In [7]:
output_dir = '/content/drive/MyDrive/IS4242/dump/'
X = joblib.load(output_dir+'X_224.pkl')
y = joblib.load(output_dir+'y_224.pkl')

In [ ]:
len(X)

817

#### Train test split

In [9]:
from sklearn.model_selection import train_test_split

# We will take 33% from 1000 for our test data.
# Recommended value 80:20, 67:33, 50:50
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

#### Augmentation only on train data

In [ ]:
augmented_X = []
augmented_y = []
for i in range(len(X_train)):
  for j in (range(10)):
      transformed = transform(image=X_train[i])
      augmented_X.append(transformed['image'])
      augmented_y.append(y_train[i])

augmented_X = np.array(augmented_X)
augmented_y = np.array(augmented_y)
X_train = np.concatenate([X_train,augmented_X])
y_train = np.concatenate([y_train,augmented_y])

#### Generate dataset of hand points

In [11]:
mp_drawing = mp.solutions.drawing_utils
mp_hands = mp.solutions.hands

In [ ]:
data = []
labels = []

In [ ]:
count = 0
with mp_hands.Hands(static_image_mode =True, max_num_hands = 2, min_detection_confidence=0.5) as hands:
    for i in tqdm(range(len(X_train))):
        # Load the image and extract its features
            results = hands.process(cv2.cvtColor(cv2.flip(X_train[i],1), cv2.COLOR_BGR2RGB))
            try:
                # Extract Hand landmarks
                for hand_landmark in results.multi_hand_landmarks:
                    right_hand = hand_landmark.landmark
                right_hand_row = list(np.array([[landmark.x, landmark.y] for landmark in right_hand]).flatten())
                # Concate rows
                row = right_hand_row

                # Extract the label from the image filename (e.g. "A.jpg")
                label = y_train[i]

                data.append(row)
                labels.append(label)
                print(row, label)
            except Exception as e:
                count += 1
                continue


  0%|          | 14/7183 [00:00<03:17, 36.34it/s]

[0.5702299475669861, 0.7003850340843201, 0.46091753244400024, 0.6018336415290833, 0.3852296471595764, 0.5265490412712097, 0.32262295484542847, 0.47085893154144287, 0.30158817768096924, 0.4085491895675659, 0.5288745164871216, 0.3980141282081604, 0.4821246862411499, 0.291260302066803, 0.4099113643169403, 0.2953939139842987, 0.3609543442726135, 0.3214380741119385, 0.5508784651756287, 0.4108913242816925, 0.3696768283843994, 0.3695741891860962, 0.363323837518692, 0.448601633310318, 0.40807145833969116, 0.464846670627594, 0.5552369356155396, 0.4376516342163086, 0.375546932220459, 0.4221045970916748, 0.3878161311149597, 0.49417614936828613, 0.4347791075706482, 0.5040949583053589, 0.5495784878730774, 0.46931031346321106, 0.4166426658630371, 0.4679672122001648, 0.42391613125801086, 0.518278181552887, 0.4663311243057251, 0.5338477492332458] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]


  0%|          | 22/7183 [00:00<04:13, 28.29it/s]

[0.44618257880210876, 0.7968925833702087, 0.3414516746997833, 0.6812290549278259, 0.30435711145401, 0.5003389716148376, 0.3140893578529358, 0.36659786105155945, 0.3157941699028015, 0.25381726026535034, 0.45740795135498047, 0.39108648896217346, 0.4473938047885895, 0.2733498215675354, 0.3924715518951416, 0.3526105284690857, 0.3555251657962799, 0.4469743072986603, 0.5481590032577515, 0.43036335706710815, 0.5281583070755005, 0.32074159383773804, 0.4578179717063904, 0.43469202518463135, 0.4192909002304077, 0.5372810363769531, 0.6377024054527283, 0.4878375828266144, 0.6066970229148865, 0.38676518201828003, 0.5277344584465027, 0.5071242451667786, 0.48841166496276855, 0.6016519069671631, 0.7347320318222046, 0.5641606450080872, 0.6992862224578857, 0.46973568201065063, 0.6206212639808655, 0.5442590713500977, 0.5745933055877686, 0.6150787472724915] [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5548228621482849, 0.4673372805118561, 0.47795143723487854, 0.500206291675

  0%|          | 30/7183 [00:00<04:14, 28.15it/s]

...

[0.5100308656692505, 0.7620093822479248, 0.4522193670272827, 0.7105070352554321, 0.4063647985458374, 0.6227877140045166, 0.3680318295955658, 0.5569956302642822, 0.3291485011577606, 0.5097253918647766, 0.4827788472175598, 0.5561599135398865, 0.5288885235786438, 0.5449478030204773, 0.5182451009750366, 0.6134046316146851, 0.4964863061904907, 0.6594330072402954, 0.5294836759567261, 0.5700717568397522, 0.566679060459137, 0.5775015354156494, 0.543979287147522, 0.6508675217628479, 0.5102813839912415, 0.6884056329727173, 0.5705419778823853, 0.5907953381538391, 0.6048387289047241, 0.5870332717895508, 0.583526611328125, 0.65013188123703, 0.5532791614532471, 0.6870617270469666, 0.6056795120239258, 0.6087965369224548, 0.6397200226783752, 0.5472373962402344, 0.6690554022789001, 0.5090805888175964, 0.6900457143783569, 0.4728260636329651] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]
[0.48484721779823303, 0.7130656242370605, 0.4255335330963135, 0.6679904460906982, 0.385854

100%|█████████▉| 7176/7183 [04:21<00:00, 21.32it/s]

[0.5366126298904419, 0.5107017159461975, 0.505510687828064, 0.5486693978309631, 0.4588738977909088, 0.5816746354103088, 0.4282485246658325, 0.6195714473724365, 0.41128942370414734, 0.654545783996582, 0.39469218254089355, 0.5245450139045715, 0.32304683327674866, 0.579613208770752, 0.27794596552848816, 0.6061011552810669, 0.24072346091270447, 0.6241232752799988, 0.39465391635894775, 0.5251433253288269, 0.33932486176490784, 0.5909715294837952, 0.3057422637939453, 0.6255792379379272, 0.27716004848480225, 0.6503888964653015, 0.40424713492393494, 0.534033477306366, 0.3938690721988678, 0.6244651079177856, 0.4261784553527832, 0.655869722366333, 0.4549906849861145, 0.6671102046966553, 0.42338141798973083, 0.5541170239448547, 0.4276798665523529, 0.6246874332427979, 0.44695398211479187, 0.6531132459640503, 0.46439146995544434, 0.6674940586090088] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5584779977798462, 0.5204808712005615, 0.5060197114944458, 0.516533076763153

100%|██████████| 7183/7183 [04:22<00:00, 27.40it/s]

[0.5632137060165405, 0.5020418763160706, 0.5154749155044556, 0.5140019655227661, 0.46063506603240967, 0.5507542490959167, 0.43084409832954407, 0.5996826887130737, 0.42395758628845215, 0.6429660320281982, 0.3983258306980133, 0.5232251882553101, 0.3297591805458069, 0.5909715294837952, 0.28353559970855713, 0.6247829794883728, 0.24550825357437134, 0.651607871055603, 0.401863694190979, 0.5320677757263184, 0.39021146297454834, 0.6240113973617554, 0.4172753095626831, 0.6626720428466797, 0.44084063172340393, 0.6819853186607361, 0.41827628016471863, 0.5501186847686768, 0.41795533895492554, 0.6375120282173157, 0.4435102939605713, 0.6663520336151123, 0.4673541188240051, 0.6800928115844727, 0.44411852955818176, 0.5745313167572021, 0.4561002254486084, 0.6330607533454895, 0.4777904748916626, 0.649634838104248, 0.49777790904045105, 0.6580288410186768] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5832306146621704, 0.45261916518211365, 0.5397135019302368, 0.4552246332168

In [ ]:
count

4706

In [ ]:
pd.DataFrame(data)

0         1         2         3         4         5         6   \
0     0.570230  0.700385  0.460918  0.601834  0.385230  0.526549  0.322623   
1     0.446183  0.796893  0.341452  0.681229  0.304357  0.500339  0.314089   
2     0.554823  0.467337  0.477951  0.500206  0.370337  0.497704  0.303738   
3     0.421717  0.593616  0.332333  0.543942  0.278878  0.457589  0.282298   
4     0.651359  0.619728  0.656911  0.514619  0.602316  0.457691  0.539696   
...        ...       ...       ...       ...       ...       ...       ...   
3156  0.583231  0.452619  0.539714  0.455225  0.495395  0.492904  0.479851   
3157  0.562530  0.498690  0.511731  0.506001  0.454501  0.544319  0.426224   
3158  0.563214  0.502042  0.515475  0.514002  0.460635  0.550754  0.430844   
3159  0.583231  0.452619  0.539714  0.455225  0.495395  0.492904  0.479851   
3160  0.628690  0.473217  0.574249  0.468687  0.512486  0.497820  0.476601   

            7         8         9   ...        32        33        34  \
0     0.470859  0.301588  0.408549  ...  0.434779  0.504095  0.549578   
1     0.366598  0.315794  0.253817  ...  0.488412  0.601652  0.734732   
2     0.458727  0.319072  0.396847  ...  0.466813  0.410920  0.478718   
3     0.384428  0.314716  0.334537  ...  0.391403  0.521059  0.528068   
4     0.429281  0.491382  0.435781  ...  0.391995  0.521948  0.437633   
...        ...       ...       ...  ...       ...       ...       ...   
3156  0.551855  0.483757  0.602373  ...  0.545168  0.576425  0.487555   
3157  0.600555  0.422746  0.650416  ...  0.465353  0.691858  0.439111   
3158  0.599683  0.423958  0.642966  ...  0.467354  0.680093  0.444119   
3159  0.551855  0.483757  0.602373  ...  0.545168  0.576425  0.487555   
3160  0.542893  0.464293  0.584233  ...  0.495103  0.641691  0.490426   

            35        36        37        38        39        40        41  
0     0.469310  0.416643  0.467967  0.423916  0.518278  0.466331  0.533848  
1     0.564161  0.699286  0.469736  0.620621  0.544259  0.574593  0.615079  
2     0.277710  0.441688  0.218711  0.420079  0.179862  0.393535  0.143242  
3     0.395230  0.475645  0.423229  0.459146  0.468935  0.459199  0.488524  
4     0.637292  0.367256  0.589515  0.384333  0.575371  0.412115  0.575475  
...        ...       ...       ...       ...       ...       ...       ...  
3156  0.524171  0.515908  0.578480  0.545968  0.580548  0.566784  0.575146  
3157  0.577353  0.453883  0.642066  0.476830  0.662664  0.497206  0.675142  
3158  0.574531  0.456100  0.633061  0.477790  0.649635  0.497778  0.658029  
3159  0.524171  0.515908  0.578480  0.545968  0.580548  0.566784  0.575146  
3160  0.535288  0.482897  0.591316  0.492581  0.618815  0.505936  0.639760  

[3161 rows x 42 columns]

In [ ]:
import joblib

output_dir = f"/content/drive/MyDrive/IS4242/dump/"
joblib.dump(data, output_dir+'data_cnn_train.pkl')
joblib.dump(labels, output_dir+'labels_cnn_train.pkl')

['/content/drive/MyDrive/IS4242/dump/labels_cnn_train.pkl']

In [8]:
import joblib
output_dir = f"/content/drive/MyDrive/IS4242/dump/"
data = joblib.load(output_dir+'data_cnn_train.pkl')
labels = joblib.load(output_dir+'labels_cnn_train.pkl')

In [ ]:
labels.shape

(3161, 24)

In [ ]:
len(X_train[0])

42

In [12]:
test_data = []
test_label = []
count = 0
with mp_hands.Hands(static_image_mode =True, max_num_hands = 2, min_detection_confidence=0.5) as hands:
    for i in tqdm(range(len(X_test))):
        # Load the image and extract its features
            results = hands.process(cv2.cvtColor(cv2.flip(X_test[i],1), cv2.COLOR_BGR2RGB))
            try:
                # Extract Hand landmarks
                for hand_landmark in results.multi_hand_landmarks:
                    right_hand = hand_landmark.landmark
                right_hand_row = list(np.array([[landmark.x, landmark.y] for landmark in right_hand]).flatten())
                # Concate rows
                row = right_hand_row

                # Extract the label from the image filename (e.g. "A.jpg")
                label = y_test[i]

                test_data.append(row)
                test_label.append(label)
                print(row, label)
            except Exception as e:
                count += 1
                continue

  3%|▎         | 5/164 [00:00<00:07, 20.97it/s]

[0.5210281014442444, 0.641315221786499, 0.39546293020248413, 0.5578718781471252, 0.3307020962238312, 0.3800443112850189, 0.3052407503128052, 0.24902814626693726, 0.2702046036720276, 0.1634766012430191, 0.41695016622543335, 0.2820096015930176, 0.4198142886161804, 0.16589711606502533, 0.42496901750564575, 0.27493152022361755, 0.43036800622940063, 0.339459091424942, 0.5108478665351868, 0.2845029830932617, 0.5148842334747314, 0.17844367027282715, 0.4996938705444336, 0.3112812340259552, 0.49929216504096985, 0.34388941526412964, 0.5973529815673828, 0.31039708852767944, 0.6130174398422241, 0.20091238617897034, 0.5859422087669373, 0.32097747921943665, 0.5842393040657043, 0.3630259037017822, 0.6818413734436035, 0.3520607650279999, 0.6982240676879883, 0.2732140123844147, 0.6630502939224243, 0.35034728050231934, 0.6547291278839111, 0.3847343325614929] [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5496582388877869, 0.6345279216766357, 0.47247281670570374, 0.625109791

  7%|▋         | 11/164 [00:00<00:06, 23.98it/s]

[0.5303622484207153, 0.7261391878128052, 0.3620838522911072, 0.6153806447982788, 0.2671659290790558, 0.40738582611083984, 0.22772908210754395, 0.24531611800193787, 0.17089855670928955, 0.12447883188724518, 0.40584099292755127, 0.294745534658432, 0.34948059916496277, 0.20392224192619324, 0.34238922595977783, 0.3307180404663086, 0.36016517877578735, 0.4387580454349518, 0.5203278064727783, 0.30517739057540894, 0.4636331796646118, 0.20133087038993835, 0.451718270778656, 0.3622964024543762, 0.46842825412750244, 0.47976988554000854, 0.6406235694885254, 0.32791975140571594, 0.569840133190155, 0.22479650378227234, 0.5453921556472778, 0.3856639564037323, 0.5597202777862549, 0.5043128728866577, 0.764388918876648, 0.36453112959861755, 0.6879178285598755, 0.2666337490081787, 0.6525718569755554, 0.3518322706222534, 0.6621406674385071, 0.42191678285598755] [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5895628929138184, 0.7734596133232117, 0.6003317832946777, 0.66376382

 13%|█▎        | 21/164 [00:00<00:05, 28.07it/s]

...

 90%|████████▉ | 147/164 [00:05<00:00, 24.19it/s]

[0.4025712013244629, 0.5869166851043701, 0.4375220537185669, 0.522254228591919, 0.5011380314826965, 0.4978063702583313, 0.5560323596000671, 0.5066971778869629, 0.5907210111618042, 0.523162841796875, 0.5285419225692749, 0.5317249298095703, 0.594545841217041, 0.5259853601455688, 0.6381144523620605, 0.5236724019050598, 0.6700278520584106, 0.5221999287605286, 0.5290641784667969, 0.5704972743988037, 0.5946837663650513, 0.5639264583587646, 0.6356530785560608, 0.556513249874115, 0.6702843308448792, 0.5516738891601562, 0.5267694592475891, 0.6048494577407837, 0.5903812050819397, 0.596366822719574, 0.632245659828186, 0.5849146842956543, 0.6661837100982666, 0.5781964659690857, 0.522779643535614, 0.6322373151779175, 0.5783458948135376, 0.6181328296661377, 0.6143463253974915, 0.6030421853065491, 0.643071711063385, 0.5925341248512268] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0.]
[0.659817636013031, 0.7055771350860596, 0.7152523994445801, 0.5528687238693237, 0.67378699779

 94%|█████████▍| 154/164 [00:06<00:00, 25.64it/s]

[0.47691941261291504, 0.7220901846885681, 0.4109916090965271, 0.6569188833236694, 0.4090764820575714, 0.5418635010719299, 0.47629427909851074, 0.4535200595855713, 0.537406325340271, 0.3900882601737976, 0.37297624349594116, 0.46395376324653625, 0.38338690996170044, 0.41171514987945557, 0.375829815864563, 0.48565569519996643, 0.363042950630188, 0.5369953513145447, 0.4320586621761322, 0.46602949500083923, 0.44608330726623535, 0.4027238190174103, 0.4247105121612549, 0.49308809638023376, 0.3995841145515442, 0.5473983287811279, 0.4899352788925171, 0.4852662682533264, 0.506833553314209, 0.4309278130531311, 0.47783714532852173, 0.5107895135879517, 0.4487495720386505, 0.5549561381340027, 0.542538046836853, 0.515808641910553, 0.5471177697181702, 0.48352673649787903, 0.5181245803833008, 0.5462149977684021, 0.4944431781768799, 0.5775335431098938] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


100%|██████████| 164/164 [00:06<00:00, 25.09it/s]


In [13]:
output_dir = f"/content/drive/MyDrive/IS4242/dump/"
joblib.dump(test_data, output_dir+'data_cnn_test.pkl')
joblib.dump(test_label, output_dir+'labels_cnn_test.pkl')

['/content/drive/MyDrive/IS4242/dump/labels_cnn_test.pkl']

In [14]:
labels = np.array(labels)
test_label = np.array(test_label)

In [20]:
from sklearn.preprocessing import StandardScaler
x_train = np.array(data)
x_test = np.array(test_data)
scaler = StandardScaler().fit(x_train)
x_train = scaler.transform(x_train)
x_test = scaler.transform(x_test)
x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))
x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))
print(x_train.shape)
print(x_test.shape)

(2645, 42, 1)
(44, 42, 1)


In [21]:
y_test.shape

(164, 24)

#### CNN Architecture with augmentation

In [22]:
# Set a learning rate annealer
learning_rate_reduction = ReduceLROnPlateau(monitor='val_accuracy', 
                                            patience=3, 
                                            verbose=1, 
                                            factor=0.5, 
                                            min_lr=0.00001)

In [23]:
# architecture
# Set the CNN model 

# One Dimensional Convolutional Neural Network model, Train will be feed to 1 Dimension Convolutional Neural Network
model = tf.keras.models.Sequential([
    tf.keras.layers.Conv1D(filters=32, kernel_size=5, strides=1, padding="causal", activation="relu", input_shape=x_train.shape[1:3]),
    tf.keras.layers.Conv1D(filters=32, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=64, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=64, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=128, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=128, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=256, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=256, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Dropout(rate=0.2),
    # Flatten the results to feed into a DNN
    tf.keras.layers.Flatten(),
    # 512 neuron hidden layer
    tf.keras.layers.Dense(512, activation='relu'), 
    tf.keras.layers.Dense(24, activation='softmax')])

model.compile(loss = 'categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_8 (Conv1D)           (None, 42, 32)            192       
                                                                 
 conv1d_9 (Conv1D)           (None, 42, 32)            5152      
                                                                 
 max_pooling1d_4 (MaxPooling  (None, 21, 32)           0         
 1D)                                                             
                                                                 
 conv1d_10 (Conv1D)          (None, 21, 64)            10304     
                                                                 
 conv1d_11 (Conv1D)          (None, 21, 64)            20544     
                                                                 
 max_pooling1d_5 (MaxPooling  (None, 10, 64)           0         
 1D)                                                  

In [24]:
epochs = 30
batch_size = 32


model_checkpoint_callback = ModelCheckpoint(
    filepath="best.h5",
    monitor='val_accuracy', 
    verbose=1, 
    save_best_only=True, 
    mode='max')

es = EarlyStopping(monitor="val_loss", mode="min", verbose=1, patience=10)

# Fit the model
history = model.fit(x_train, labels, batch_size=batch_size,
                              epochs = epochs, validation_data = (x_test, test_label),steps_per_epoch=x_train.shape[0] // batch_size,
                              verbose = 1,   callbacks=[model_checkpoint_callback,learning_rate_reduction,es])

Epoch 1/30
80/82 [============================>.] - ETA: 0s - loss: 3.0623 - accuracy: 0.0770
Epoch 1: val_accuracy improved from -inf to 0.13636, saving model to best.h5
82/82 [==============================] - 4s 13ms/step - loss: 3.0583 - accuracy: 0.0774 - val_loss: 2.8459 - val_accuracy: 0.1364 - lr: 0.0010
Epoch 2/30
80/82 [============================>.] - ETA: 0s - loss: 2.4799 - accuracy: 0.2052
Epoch 2: val_accuracy improved from 0.13636 to 0.34091, saving model to best.h5
82/82 [==============================] - 1s 10ms/step - loss: 2.4715 - accuracy: 0.2067 - val_loss: 2.1105 - val_accuracy: 0.3409 - lr: 0.0010
Epoch 3/30
76/82 [==========================>...] - ETA: 0s - loss: 1.8268 - accuracy: 0.3879
Epoch 3: val_accuracy improved from 0.34091 to 0.45455, saving model to best.h5
82/82 [==============================] - 1s 10ms/step - loss: 1.8203 - accuracy: 0.3873 - val_loss: 1.6714 - val_accuracy: 0.4545 - lr: 0.0010
Epoch 4/30
82/82 [==============================] - 

#### Prediction and evaluation

In [25]:
results = model.predict(x_test)
y_pred = np.argmax(results,axis = 1) 
y_true = np.argmax(test_label,axis = 1) 


2/2 [==============================] - 0s 6ms/step


In [26]:
from sklearn.metrics import classification_report
print(classification_report(y_true, y_pred))

              precision    recall  f1-score   support

           0       0.75      1.00      0.86         3
           1       0.00      0.00      0.00         1
           2       0.67      1.00      0.80         2
           3       1.00      1.00      1.00         1
           4       0.67      1.00      0.80         2
           6       1.00      1.00      1.00         1
           7       1.00      1.00      1.00         2
           8       1.00      0.50      0.67         2
           9       0.00      0.00      0.00         1
          10       1.00      0.67      0.80         3
          11       0.00      0.00      0.00         1
          12       0.50      1.00      0.67         2
          13       1.00      0.50      0.67         2
          14       1.00      1.00      1.00         3
          16       0.67      0.67      0.67         3
          17       0.00      0.00      0.00         1
          18       0.75      1.00      0.86         3
          19       0.00    

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [27]:
from sklearn.metrics import roc_auc_score
import numpy as np

# Calculate the ROC AUC using the micro-averaging method
roc_auc = roc_auc_score(test_label, results, multi_class='ovo', average='micro')
print("ROC AUC score:", roc_auc)


ROC AUC score: 0.9737693136902623


Train on whole dataset

In [30]:
augmented_X = []
augmented_y = []
for i in range(len(X)):
  for j in (range(10)):
      transformed = transform(image=X[i])
      augmented_X.append(transformed['image'])
      augmented_y.append(y[i])

augmented_X = np.array(augmented_X)
augmented_y = np.array(augmented_y)
X = np.concatenate([X,augmented_X])
y = np.concatenate([y,augmented_y])

In [31]:
mp_drawing = mp.solutions.drawing_utils
mp_hands = mp.solutions.hands

In [32]:
data = []
labels = []

In [33]:
count = 0
with mp_hands.Hands(static_image_mode =True, max_num_hands = 2, min_detection_confidence=0.5) as hands:
    for i in tqdm(range(len(X))):
        # Load the image and extract its features
            results = hands.process(cv2.cvtColor(cv2.flip(X[i],1), cv2.COLOR_BGR2RGB))
            try:
                # Extract Hand landmarks
                for hand_landmark in results.multi_hand_landmarks:
                    right_hand = hand_landmark.landmark
                right_hand_row = list(np.array([[landmark.x, landmark.y] for landmark in right_hand]).flatten())
                # Concate rows
                row = right_hand_row

                # Extract the label from the image filename (e.g. "A.jpg")
                label = y[i]

                data.append(row)
                labels.append(label)
                print(row, label)
            except Exception as e:
                count += 1
                continue


  0%|          | 4/8987 [00:00<10:19, 14.50it/s]

[0.6893226504325867, 0.511483371257782, 0.6227255463600159, 0.3735395073890686, 0.4887554943561554, 0.28191471099853516, 0.3812757432460785, 0.3104405701160431, 0.34841203689575195, 0.38644298911094666, 0.5468429923057556, 0.3439619541168213, 0.36343029141426086, 0.340884268283844, 0.26849180459976196, 0.34165167808532715, 0.18735185265541077, 0.350254625082016, 0.5508190393447876, 0.458968847990036, 0.3323928415775299, 0.4467167258262634, 0.21754077076911926, 0.42757129669189453, 0.13726866245269775, 0.42436519265174866, 0.5486301183700562, 0.5688624978065491, 0.33767640590667725, 0.544520378112793, 0.3706008195877075, 0.5084154009819031, 0.43465307354927063, 0.496858686208725, 0.5388574004173279, 0.6581798791885376, 0.3714066743850708, 0.6336698532104492, 0.40209564566612244, 0.6014752984046936, 0.46330854296684265, 0.5952752828598022] [0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.4842866063117981, 0.6252379417419434, 0.5922341346740723, 0.6995348334312

  0%|          | 8/8987 [00:00<09:36, 15.57it/s]

[0.25806209444999695, 0.512768566608429, 0.3861837387084961, 0.6130593419075012, 0.5580868721008301, 0.6335543394088745, 0.6616803407669067, 0.5998389720916748, 0.7085224986076355, 0.5246628522872925, 0.6692732572555542, 0.4358067214488983, 0.7552158832550049, 0.39885687828063965, 0.6671687364578247, 0.48235023021698, 0.5879429578781128, 0.5220650434494019, 0.6056863069534302, 0.33408498764038086, 0.6853700876235962, 0.26887047290802, 0.5931093096733093, 0.3855102062225342, 0.5276396870613098, 0.4373794496059418, 0.5158966183662415, 0.25747454166412354, 0.5885308384895325, 0.19707173109054565, 0.5057290196418762, 0.3221569061279297, 0.4550556540489197, 0.3843718469142914, 0.40786048769950867, 0.20071808993816376, 0.448904424905777, 0.17031952738761902, 0.40396618843078613, 0.26387691497802734, 0.3687177300453186, 0.32118678092956543] [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5673684477806091, 0.10421079397201538, 0.3995620012283325, 0.218880295753479,

  0%|          | 19/8987 [00:01<07:52, 18.98it/s]

...

[0.44468092918395996, 0.8248838186264038, 0.3415975272655487, 0.7727130651473999, 0.25635215640068054, 0.694827139377594, 0.21996605396270752, 0.6352942585945129, 0.23905226588249207, 0.6029480695724487, 0.378768652677536, 0.5058338046073914, 0.34638872742652893, 0.4372249245643616, 0.3112649619579315, 0.49535444378852844, 0.29383590817451477, 0.5579354166984558, 0.47860074043273926, 0.4891270101070404, 0.4570732116699219, 0.339107871055603, 0.4607519805431366, 0.24597647786140442, 0.4676460325717926, 0.1668030023574829, 0.5741598010063171, 0.5209016799926758, 0.6093428730964661, 0.38404062390327454, 0.6348249912261963, 0.3026847243309021, 0.6542223691940308, 0.23453491926193237, 0.6613731384277344, 0.5896028876304626, 0.7478007674217224, 0.5056972503662109, 0.7997682690620422, 0.4565744698047638, 0.8400645852088928, 0.40740767121315] [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


100%|█████████▉| 8983/8987 [07:40<00:00, 22.43it/s]

[0.5639995336532593, 0.5670773386955261, 0.46958568692207336, 0.5165013074874878, 0.3842511475086212, 0.46885403990745544, 0.29933416843414307, 0.46406567096710205, 0.20754244923591614, 0.452457994222641, 0.6342567801475525, 0.3156072199344635, 0.5864441990852356, 0.4061237573623657, 0.5018202066421509, 0.46843960881233215, 0.4520973265171051, 0.5110291242599487, 0.7489814758300781, 0.4135574698448181, 0.5747362375259399, 0.5717564821243286, 0.47932830452919006, 0.6068780422210693, 0.45289096236228943, 0.6011015176773071, 0.7938117980957031, 0.5240638852119446, 0.5992177128791809, 0.649931788444519, 0.5188702940940857, 0.6721547245979309, 0.507935106754303, 0.6605225801467896, 0.8024623990058899, 0.6448496580123901, 0.6477879285812378, 0.7360521554946899, 0.569482684135437, 0.7452455759048462, 0.5490157604217529, 0.7345958352088928] [0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5640746355056763, 0.5573098659515381, 0.47566622495651245, 0.5092434883117676,

100%|██████████| 8987/8987 [07:40<00:00, 19.51it/s]

[0.5855486989021301, 0.7103063464164734, 0.4879365563392639, 0.5976280570030212, 0.40454626083374023, 0.5207654237747192, 0.30371612310409546, 0.47730809450149536, 0.2065015733242035, 0.45497363805770874, 0.6355492472648621, 0.39947572350502014, 0.4725332260131836, 0.5265135765075684, 0.39976194500923157, 0.5608131885528564, 0.3643852472305298, 0.5712345838546753, 0.7085227966308594, 0.5031993985176086, 0.45561978220939636, 0.6431041955947876, 0.39121824502944946, 0.656785786151886, 0.38986295461654663, 0.6497425436973572, 0.7392514944076538, 0.6329663395881653, 0.47190892696380615, 0.7640525698661804, 0.4066694974899292, 0.7650429010391235, 0.4049866199493408, 0.7419365644454956, 0.7440750002861023, 0.7646315097808838, 0.547482430934906, 0.8372325897216797, 0.4608234763145447, 0.8188324570655823, 0.42293447256088257, 0.7914180755615234] [0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0.5640746355056763, 0.5573098659515381, 0.47566622495651245, 0.509243488311

In [34]:
len(data)

2957

In [35]:
joblib.dump(data, 'combined_data.pkl')
joblib.dump(labels, 'combined_labels.pkl')


['combined_labels.pkl']

In [36]:
labels = np.array(labels)
data = np.array(data)

In [37]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler().fit(data)
x = scaler.transform(data)
x = np.reshape(x, (x.shape[0], x.shape[1], 1))
print(x.shape)

(2957, 42, 1)


In [38]:
labels.shape

(2957, 24)

#### CNN Architecture with augmentation

In [44]:
# architecture
# Set the CNN model 

# One Dimensional Convolutional Neural Network model, Train will be feed to 1 Dimension Convolutional Neural Network
model = tf.keras.models.Sequential([
    tf.keras.layers.Conv1D(filters=32, kernel_size=5, strides=1, padding="causal", activation="relu", input_shape=x_train.shape[1:3]),
    tf.keras.layers.Conv1D(filters=32, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=64, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=64, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=128, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=128, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Conv1D(filters=256, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.Conv1D(filters=256, kernel_size=5, strides=1, padding="causal", activation="relu"),
    tf.keras.layers.MaxPooling1D(pool_size=2),
    tf.keras.layers.Dropout(rate=0.2),
    # Flatten the results to feed into a DNN
    tf.keras.layers.Flatten(),
    # 512 neuron hidden layer
    tf.keras.layers.Dense(512, activation='relu'), 
    tf.keras.layers.Dense(24, activation='softmax')])

model.compile(loss = 'categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

Model: "sequential_3"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_24 (Conv1D)          (None, 42, 32)            192       
                                                                 
 conv1d_25 (Conv1D)          (None, 42, 32)            5152      
                                                                 
 max_pooling1d_12 (MaxPoolin  (None, 21, 32)           0         
 g1D)                                                            
                                                                 
 conv1d_26 (Conv1D)          (None, 21, 64)            10304     
                                                                 
 conv1d_27 (Conv1D)          (None, 21, 64)            20544     
                                                                 
 max_pooling1d_13 (MaxPoolin  (None, 10, 64)           0         
 g1D)                                                 

In [45]:
epochs = 30
batch_size = 32

# Fit the model
history = model.fit(x, labels, batch_size=batch_size,
                              epochs = epochs,steps_per_epoch=x.shape[0] // batch_size,
                              verbose = 1)

Epoch 1/30
92/92 [==============================] - 4s 8ms/step - loss: 2.9550 - accuracy: 0.1101
Epoch 2/30
92/92 [==============================] - 1s 8ms/step - loss: 2.3324 - accuracy: 0.2520
Epoch 3/30
92/92 [==============================] - 1s 8ms/step - loss: 1.7452 - accuracy: 0.4099
Epoch 4/30
92/92 [==============================] - 1s 8ms/step - loss: 1.3026 - accuracy: 0.5593
Epoch 5/30
92/92 [==============================] - 1s 8ms/step - loss: 0.9512 - accuracy: 0.6906
Epoch 6/30
92/92 [==============================] - 1s 8ms/step - loss: 0.7261 - accuracy: 0.7549
Epoch 7/30
92/92 [==============================] - 1s 14ms/step - loss: 0.5972 - accuracy: 0.8109
Epoch 8/30
92/92 [==============================] - 2s 19ms/step - loss: 0.4976 - accuracy: 0.8424
Epoch 9/30
92/92 [==============================] - 1s 12ms/step - loss: 0.3892 - accuracy: 0.8735
Epoch 10/30
92/92 [==============================] - 1s 8ms/step - loss: 0.3837 - accuracy: 0.8766
Epoch 11/30
92/9

In [50]:
model.save('cnn.h5')

#### Prediction and evaluation

In [46]:
results = model.predict(x)
y_pred = np.argmax(results,axis = 1) 
y_true = np.argmax(labels,axis = 1) 


93/93 [==============================] - 0s 3ms/step


In [47]:
from sklearn.metrics import classification_report
print(classification_report(y_true, y_pred))

              precision    recall  f1-score   support

           0       0.97      1.00      0.99       132
           1       1.00      0.99      1.00       137
           2       0.99      0.98      0.98       142
           3       0.96      1.00      0.98       108
           4       1.00      0.99      1.00       127
           5       1.00      1.00      1.00       136
           6       1.00      1.00      1.00       143
           7       0.99      1.00      1.00       130
           8       1.00      0.96      0.98        96
           9       1.00      0.95      0.97       101
          10       0.99      1.00      1.00       131
          11       0.97      1.00      0.98        86
          12       1.00      0.97      0.98        99
          13       0.96      0.99      0.97        94
          14       0.99      1.00      1.00       125
          15       1.00      1.00      1.00       104
          16       0.99      0.95      0.97       111
          17       1.00    

In [49]:
from sklearn.metrics import roc_auc_score
import numpy as np

# Calculate the ROC AUC using the micro-averaging method
roc_auc = roc_auc_score(labels, results, multi_class='ovo', average='micro')
print("ROC AUC score:", roc_auc)


ROC AUC score: 0.9999648945765487
